see: http://millionsongdataset.com/pages/getting-dataset/#subset

In [ ]:
# !wget http://labrosa.ee.columbia.edu/~dpwe/tmp/millionsongsubset.tar.gz
# !tar -xvzf millionsongsubset.tar.gz

In [ ]:
# !pip install pandas h5py pyarrow fastparquet

In [2]:
import os
import h5py
import pandas as pd
from tqdm.auto import tqdm

import unibox as ub

In [ ]:
len(ub.ls("../data/MillionSongSubset", [".h5"]))

Listing local files: 0files [00:00, ?files/s]

10000

In [5]:
import os
import pandas as pd
import numpy as np
import hdf5_getters
import h5py
from tqdm import tqdm
from concurrent.futures import ProcessPoolExecutor

# Define dataset path
dataset_path = "/lv0/yada/dataproc5/data/MillionSongSubset"

# Function to extract all available fields from an HDF5 file
def extract_song_data(file_path):
    """Extracts all available fields from an HDF5 song file using hdf5_getters."""
    song_data = {}

    try:
        with hdf5_getters.open_h5_file_read(file_path) as h5:
            # Get all getter functions from hdf5_getters
            getters = [func for func in dir(hdf5_getters) if func.startswith("get_")]

            for getter in getters:
                try:
                    # Dynamically call each getter function
                    value = getattr(hdf5_getters, getter)(h5)

                    # Optimize conversions
                    if isinstance(value, np.ndarray):
                        value = value.tolist()
                    elif isinstance(value, bytes):
                        value = value.decode()

                    # Store in dictionary with a cleaned-up key name
                    song_data[getter[4:]] = value

                except Exception:
                    continue  # Skip errors but don't slow down

    except Exception as e:
        print(f"Error processing {file_path}: {e}")
    
    return song_data

# Function to process multiple files in parallel
def process_files_in_parallel(h5_files, num_workers=8):
    """Processes multiple .h5 files in parallel."""
    all_songs = []

    with ProcessPoolExecutor(max_workers=num_workers) as executor:
        for song_data in tqdm(executor.map(extract_song_data, h5_files), total=len(h5_files)):
            if song_data:
                all_songs.append(song_data)
    
    return all_songs

# Find all .h5 files
h5_files = [os.path.join(root, file) for root, _, files in os.walk(dataset_path) for file in files if file.endswith(".h5")]

# Process files in parallel
all_songs = process_files_in_parallel(h5_files, num_workers=24)

# Convert to Pandas DataFrame
df = pd.DataFrame(all_songs)

100%|██████████| 10000/10000 [00:39<00:00, 250.36it/s]


In [9]:
ub.peeks(df)

(10000, 55)
Index(['analysis_sample_rate', 'artist_7digitalid', 'artist_familiarity',
       'artist_hotttnesss', 'artist_id', 'artist_latitude', 'artist_location',
       'artist_longitude', 'artist_mbid', 'artist_mbtags',
       'artist_mbtags_count', 'artist_name', 'artist_playmeid', 'artist_terms',
       'artist_terms_freq', 'artist_terms_weight', 'audio_md5',
       'bars_confidence', 'bars_start', 'beats_confidence', 'beats_start',
       'danceability', 'duration', 'end_of_fade_in', 'energy', 'key',
       'key_confidence', 'loudness', 'mode', 'mode_confidence', 'num_songs',
       'release', 'release_7digitalid', 'sections_confidence',
       'sections_start', 'segments_confidence', 'segments_loudness_max',
       'segments_loudness_max_time', 'segments_loudness_start',
       'segments_pitches', 'segments_start', 'segments_timbre',
       'similar_artists', 'song_hotttnesss', 'song_id', 'start_of_fade_out',
       'tatums_confidence', 'tatums_start', 'tempo', 'time_signature'

analysis_sample_rate  artist_7digitalid  artist_familiarity  \
0                 22050             174717            0.450743   
1                 22050               7173            0.392710   
2                 22050               2759            0.602767   

   artist_hotttnesss           artist_id  artist_latitude artist_location  \
0           0.331215  AR1DGSO1187FB59B15              NaN                   
1           0.311789  ARO6WZY1187FB3A86E              NaN                   
2           0.463193  ARH1LE01187B98D68D              NaN                   

   artist_longitude                           artist_mbid  \
0               NaN  fe4e71a9-ddb9-47b5-9e2e-ec53862a91c6   
1               NaN  23f7ad3f-a189-4a1c-9991-4763ded495a7   
2               NaN  3df3a779-a7b1-4362-a8b4-9ae6c7eb623d   

                  artist_mbtags  ... start_of_fade_out  \
0                            []  ...           266.879   
1                            []  ...           321.300   
2  [b'american', b'soundtrack']  ...            67.895   

                                   tatums_confidence  \
0  [0.0, 0.0, 0.896, 0.819, 0.664, 0.693, 0.67, 0...   
1  [0.451, 0.426, 0.396, 0.32, 0.255, 0.204, 0.15...   
2  [0.056, 0.058, 0.056, 0.059, 0.097, 0.093, 0.0...   

                                        tatums_start    tempo time_signature  \
0  [0.16738, 0.44887, 0.73036, 1.09072, 1.44407, ...  107.053              4   
1  [0.05024, 0.25641, 0.46357, 0.66974, 0.87691, ...  149.853              3   
2  [0.54095, 0.86496, 1.20205, 1.52933, 1.85662, ...   91.249              4   

  time_signature_confidence                title track_7digitalid  \
0                     0.657                 Jody          2555900   
1                     1.000  Turntable Terrorist          5591259   
2                     0.568        Porcelain Man          7341937   

             track_id  year  
0  TRAHHUN128F4227029     0  
1  TRAHHMM128F932D5D9  1995  
2  TRAHHJY12903CA73BD  1999  

[3 rows x 55 columns]

In [8]:
ub.saves(df, "hf://trojblue/million-song-subset", private=False)

2025-02-19 14:01:45 [INFO] HuggingFaceDatasetsBackend.data_to_hub: Uploading dataset to HF repo trojblue/million-song-subset


Uploading the dataset shards:   0%|          | 0/5 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/20 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/20 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/20 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/20 [00:00<?, ?ba/s]

Creating parquet from Arrow format:   0%|          | 0/20 [00:00<?, ?ba/s]

2025-02-19 14:02:47 [INFO] saves: DataFrame saved (HF dataset) to "hf://trojblue/million-song-subset" in 62.75s
